In [1]:
import os
os.environ["CUDA_DEVICE_ORDER"]="PCI_BUS_ID"
os.environ["CUDA_VISIBLE_DEVICES"]="0"
#os.environ["TF_CPP_MIN_LOG_LEVEL"] = "3" 
from tensorflow.python.client import device_lib
print device_lib.list_local_devices()

[name: "/device:CPU:0"
device_type: "CPU"
memory_limit: 268435456
locality {
}
incarnation: 5026612345973606235
, name: "/device:GPU:0"
device_type: "GPU"
memory_limit: 11983277261
locality {
  bus_id: 1
}
incarnation: 3737456979940513296
physical_device_desc: "device: 0, name: TITAN X (Pascal), pci bus id: 0000:05:00.0, compute capability: 6.1"
]


In [1]:
import tensorflow as tf
import numpy as np
import numpy.matlib
from time import time
from StochasticDropoutNet_unrolled import StochasticDropoutNet
from util import xor_data, extract_update_dict
from tensorflow.examples.tutorials.mnist import input_data
mnist = input_data.read_data_sets('MNIST_data', one_hot=False)

Extracting MNIST_data/train-images-idx3-ubyte.gz
Extracting MNIST_data/train-labels-idx1-ubyte.gz
Extracting MNIST_data/t10k-images-idx3-ubyte.gz
Extracting MNIST_data/t10k-labels-idx1-ubyte.gz


In [3]:
# model = StochasticDropoutNet(min_dropout_rate = 0.001, max_dropout_rate = 0.001, num_weight_train_steps = 64)
model = StochasticDropoutNet(min_init_dropout_rate = 0.4, 
                             max_init_dropout_rate = 0.6,
                             train_batch_size = 50,
                             valid_batch_size = 500,
                             unroll_steps = 5,
                             num_weight_train_steps = 4,
                             head = 1,
                             log_dir = "/mnt/hdd1/kqian3/rl_struct/")

Tensor("Slice:0", shape=(?, 28, 28, 1), dtype=float32)
Tensor("Slice_1:0", shape=(?, 14, 14, 1), dtype=float32)
Tensor("Slice_2:0", shape=(?, 1, 1, 1), dtype=float32)
[<tf.Tensor 'StopGradient_3:0' shape=(4, 4, 1) dtype=float32>, <tf.Tensor 'StopGradient_4:0' shape=(2, 2, 1) dtype=float32>, <tf.Tensor 'StopGradient_5:0' shape=(1, 1, 1) dtype=float32>]


In [4]:
model.saver.restore(model.sess, "{}model_unroll-15".format("/mnt/hdd1/kqian3/rl_struct/"))

INFO:tensorflow:Restoring parameters from /mnt/hdd1/kqian3/rl_struct/model_unroll-15


In [28]:
inputs_train, targets_train = mnist.train.next_batch(50)
#inputs_train = np.matlib.repmat(inputs_train, 10000, 1)
#targets_train = np.matlib.repmat(targets_train, 10000, 1)[:,0]
inputs_train = inputs_train.reshape((-1, 28, 28, 1))
feed_dict = {model.inputs: inputs_train,
             model.targets: targets_train}
tidu = tf.gradients(model.unrolled_loss, model.struct_param)

In [41]:
j = 2
grad = model.sess.run(tidu, feed_dict = feed_dict)

# original value
original_value = model.sess.run(model.struct_param[0][0,j,0])
#model.sess.run(tf.assign(model.struct_param[0][0,j,0], 0 * original_value))
loss1 = model.sess.run(model.unrolled_loss_true, feed_dict = feed_dict)
model.sess.run(tf.assign(model.struct_param[0][0,j,0], original_value + 0.1))
loss2 = model.sess.run(model.unrolled_loss_true, feed_dict = feed_dict)
model.sess.run(tf.assign(model.struct_param[0][0,j,0], original_value))
print(grad[0][0,j,0])
print((loss2-loss1)/0.1)

0.5088327
-1.104750633239746


In [4]:
a = tf.ones([3, 3, 3])
b = tf.slice(a, [0, 0, 0], [-1, 2, 2])
print(b)

Tensor("Slice_1:0", shape=(3, 2, 2), dtype=float32)


In [6]:
j = 4
grads = []
approx = []
tic = time()
with tf.device('/gpu:0'):
    for _ in range(3): 
        loss1 = model.sess.run(model.unrolled_loss_true, feed_dict = feed_dict)
        grad = model.sess.run(tf.gradients(model.unrolled_loss, model.struct_param), feed_dict = feed_dict)
        model.sess.run(tf.assign(model.struct_param[0][0,j,0], model.sess.run(model.struct_param[0][0,j,0]) + 0.1))
        loss2 = model.sess.run(model.unrolled_loss_true, feed_dict = feed_dict)
        model.sess.run(tf.assign(model.struct_param[0][0,j,0], model.sess.run(model.struct_param[0][0,j,0]) - 0.1))
        grads.append(grad[0][0,j,0])
        approx.append((loss2-loss1)/0.1)
print(time()-tic)
print(grads/300)
print(approx/300)

27.974905014


TypeError: unsupported operand type(s) for /: 'list' and 'int'

In [4]:
from util import tf_repeat
import tensorflow as tf
a = tf.constant([[1,2,3],[4,5,6]])
b = tf_repeat(a, [2, 3])

with tf.Session() as sess:
    print(b.eval())

[[1 1 1 2 2 2 3 3 3]
 [1 1 1 2 2 2 3 3 3]
 [4 4 4 5 5 5 6 6 6]
 [4 4 4 5 5 5 6 6 6]]


In [ ]:
inputs_train, targets_train = mnist.train.next_batch(32)
inputs_train = inputs_train.reshape((-1, 28, 28, 1))
inputs_valid, targets_valid = mnist.validation.next_batch(32)
inputs_valid = inputs_valid.reshape((-1, 28, 28, 1))
feed_dict = {model.inputs: inputs_train[0 : 32, ...],
             model.targets: targets_train[0 : 32, ...]}
print(model.sess.run([model.valid_index, tf.gradients(model.loss, model.struct_param)], feed_dict = feed_dict))


In [17]:
inputs_train, targets_train = mnist.train.next_batch(55000)
inputs_train = inputs_train.reshape((-1, 28, 28, 1))
inputs_valid, targets_valid = mnist.validation.next_batch(5000)
inputs_valid = inputs_valid.reshape((-1, 28, 28, 1))

model.train_unroll(inputs_train, targets_train, inputs_valid, targets_valid, num_epochs = 15)
#model.train_fine_tune(inputs_train, targets_train, inputs_valid, targets_valid, num_epochs = 20)

Extracting MNIST_data/train-images-idx3-ubyte.gz
Extracting MNIST_data/train-labels-idx1-ubyte.gz
Extracting MNIST_data/t10k-images-idx3-ubyte.gz
Extracting MNIST_data/t10k-labels-idx1-ubyte.gz
Epoch 1, weight train batch 0, step 0, loss = 2.32563900948, accuracy = 0.159999996424
struct_param_value = [array([[[0.5095842 ],
        [0.52549195],
        [0.5169494 ],
        [0.5293247 ]],

       [[0.52108544],
        [0.41298112],
        [0.56004286],
        [0.53589225]],

       [[0.44344714],
        [0.5732036 ],
        [0.5901452 ],
        [0.46218097]],

       [[0.5446369 ],
        [0.56796855],
        [0.5206318 ],
        [0.43542692]]], dtype=float32), array([[[0.42315516],
        [0.51581746]],

       [[0.5277031 ],
        [0.5076022 ]]], dtype=float32), array([[[0.56874776]]], dtype=float32)]
valid_index = [array([[[1.],
        [1.],
        [1.],
        [1.],
        [1.],
        [1.],
        [1.],
        [1.],
        [1.],
        [1.],
        [1.],
    

Test accuracy =0.108200000226
Epoch 1, weight train batch 1, step 1, loss = 2.33212184906, accuracy = 0.119999997318
Epoch 1, weight train batch 2, step 2, loss = 2.27567076683, accuracy = 0.140000000596
Epoch 1, weight train batch 3, step 3, loss = 2.30598044395, accuracy = 0.0799999982119
Epoch 1, weight train batch 4, step 0, loss = 2.29644012451, accuracy = 0.180000007153
Epoch 1, weight train batch 5, step 1, loss = 2.31332755089, accuracy = 0.119999997318
Epoch 1, weight train batch 6, step 2, loss = 2.32231283188, accuracy = 0.10000000149
Epoch 1, weight train batch 7, step 3, loss = 2.29222583771, accuracy = 0.140000000596
Epoch 1, weight train batch 8, step 0, loss = 2.29667592049, accuracy = 0.140000000596
Epoch 1, weight train batch 9, step 1, loss = 2.27728796005, accuracy = 0.10000000149
Epoch 1, weight train batch 10, step 2, loss = 2.3043076992, accuracy = 0.10000000149
Epoch 1, weight train batch 11, step 3, loss = 2.30091047287, accuracy = 0.0599999986589
Epoch 1, weig

Epoch 1, weight train batch 107, step 3, loss = 2.3036441803, accuracy = 0.10000000149
Epoch 1, weight train batch 108, step 0, loss = 2.30359458923, accuracy = 0.180000007153
Epoch 1, weight train batch 109, step 1, loss = 2.29922294617, accuracy = 0.239999994636
Epoch 1, weight train batch 110, step 2, loss = 2.30231022835, accuracy = 0.10000000149
Epoch 1, weight train batch 111, step 3, loss = 2.30560278893, accuracy = 0.140000000596
Epoch 1, weight train batch 112, step 0, loss = 2.29810905457, accuracy = 0.159999996424
Epoch 1, weight train batch 113, step 1, loss = 2.29971599579, accuracy = 0.159999996424
Epoch 1, weight train batch 114, step 2, loss = 2.29632592201, accuracy = 0.119999997318
Epoch 1, weight train batch 115, step 3, loss = 2.30458498001, accuracy = 0.0799999982119
Epoch 1, weight train batch 116, step 0, loss = 2.30433726311, accuracy = 0.140000000596
Epoch 1, weight train batch 117, step 1, loss = 2.30984401703, accuracy = 0.0799999982119
Epoch 1, weight train 

Epoch 1, weight train batch 207, step 3, loss = 2.30515480042, accuracy = 0.10000000149
Epoch 1, weight train batch 208, step 0, loss = 2.30390524864, accuracy = 0.0599999986589
Epoch 1, weight train batch 209, step 1, loss = 2.29683184624, accuracy = 0.140000000596
Epoch 1, weight train batch 210, step 2, loss = 2.29398941994, accuracy = 0.159999996424
Epoch 1, weight train batch 211, step 3, loss = 2.30019617081, accuracy = 0.119999997318
Epoch 1, weight train batch 212, step 0, loss = 2.30128860474, accuracy = 0.119999997318
Epoch 1, weight train batch 213, step 1, loss = 2.30361700058, accuracy = 0.159999996424
Epoch 1, weight train batch 214, step 2, loss = 2.30123996735, accuracy = 0.140000000596
Epoch 1, weight train batch 215, step 3, loss = 2.30334830284, accuracy = 0.20000000298
Epoch 1, weight train batch 216, step 0, loss = 2.30231785774, accuracy = 0.0599999986589
Epoch 1, weight train batch 217, step 1, loss = 2.29806113243, accuracy = 0.180000007153
Epoch 1, weight train

Epoch 1, weight train batch 317, step 1, loss = 2.30157375336, accuracy = 0.180000007153
Epoch 1, weight train batch 318, step 2, loss = 2.29892373085, accuracy = 0.159999996424
Epoch 1, weight train batch 319, step 3, loss = 2.29876089096, accuracy = 0.140000000596
Epoch 1, weight train batch 320, step 0, loss = 2.30428814888, accuracy = 0.0799999982119
Epoch 1, weight train batch 321, step 1, loss = 2.31357169151, accuracy = 0.0599999986589
Epoch 1, weight train batch 322, step 2, loss = 2.30334830284, accuracy = 0.159999996424
Epoch 1, weight train batch 323, step 3, loss = 2.30590033531, accuracy = 0.159999996424
Epoch 1, weight train batch 324, step 0, loss = 2.29590678215, accuracy = 0.20000000298
Epoch 1, weight train batch 325, step 1, loss = 2.29573202133, accuracy = 0.159999996424
Epoch 1, weight train batch 326, step 2, loss = 2.30466294289, accuracy = 0.10000000149
Epoch 1, weight train batch 327, step 3, loss = 2.3215136528, accuracy = 0.0399999991059
Epoch 1, weight train

...

Epoch 14, weight train batch 889, step 1, loss = 1.85814142227, accuracy = 0.300000011921
Epoch 14, weight train batch 890, step 2, loss = 2.07212519646, accuracy = 0.219999998808
Epoch 14, weight train batch 891, step 3, loss = 1.88963007927, accuracy = 0.259999990463
Epoch 14, struct train step 224, loss = 1.97295260429, accuracy = 0.256000012159
Epoch 14, weight train batch 892, step 0, loss = 2.11642885208, accuracy = 0.180000007153
Epoch 14, weight train batch 893, step 1, loss = 2.10856342316, accuracy = 0.219999998808
Epoch 14, weight train batch 894, step 2, loss = 1.88361907005, accuracy = 0.180000007153
Epoch 14, weight train batch 895, step 3, loss = 2.03866553307, accuracy = 0.300000011921
Epoch 14, struct train step 225, loss = 2.00417780876, accuracy = 0.21400000155
Epoch 14, weight train batch 896, step 0, loss = 1.87693202496, accuracy = 0.159999996424
Epoch 14, weight train batch 897, step 1, loss = 1.85384273529, accuracy = 0.319999992847
Epoch 14, weight train batch 

Epoch 14, struct train step 227, loss = 1.98103761673, accuracy = 0.233999997377
Epoch 14, weight train batch 904, step 0, loss = 1.92902135849, accuracy = 0.319999992847
Epoch 14, weight train batch 905, step 1, loss = 1.95974576473, accuracy = 0.159999996424
Epoch 14, weight train batch 906, step 2, loss = 1.91782701015, accuracy = 0.20000000298
Epoch 14, weight train batch 907, step 3, loss = 1.91483068466, accuracy = 0.300000011921
Epoch 14, struct train step 228, loss = 1.95501554012, accuracy = 0.217999994755
Epoch 14, weight train batch 908, step 0, loss = 2.05896615982, accuracy = 0.20000000298
Epoch 14, weight train batch 909, step 1, loss = 2.00081777573, accuracy = 0.239999994636
Epoch 14, weight train batch 910, step 2, loss = 2.0081949234, accuracy = 0.219999998808
Epoch 14, weight train batch 911, step 3, loss = 2.01502537727, accuracy = 0.159999996424
Epoch 14, struct train step 229, loss = 1.96799433231, accuracy = 0.261999994516
Epoch 14, weight train batch 912, step 0

Epoch 14, weight train batch 981, step 1, loss = 1.95131540298, accuracy = 0.159999996424
Epoch 14, weight train batch 982, step 2, loss = 1.98715054989, accuracy = 0.259999990463
Epoch 14, weight train batch 983, step 3, loss = 2.03339314461, accuracy = 0.219999998808
Epoch 14, struct train step 247, loss = 1.93242681026, accuracy = 0.246000006795
Epoch 14, weight train batch 984, step 0, loss = 2.08290576935, accuracy = 0.20000000298
Epoch 14, weight train batch 985, step 1, loss = 1.98564636707, accuracy = 0.119999997318
Epoch 14, weight train batch 986, step 2, loss = 1.91395294666, accuracy = 0.180000007153
Epoch 14, weight train batch 987, step 3, loss = 1.8518961668, accuracy = 0.20000000298
Epoch 14, struct train step 248, loss = 1.96703350544, accuracy = 0.21400000155
Epoch 14, weight train batch 988, step 0, loss = 2.09189033508, accuracy = 0.140000000596
Epoch 14, weight train batch 989, step 1, loss = 2.06432771683, accuracy = 0.219999998808
Epoch 14, weight train batch 990

Epoch 14, struct train step 253, loss = 1.9541093111, accuracy = 0.219999998808
Epoch 14, weight train batch 1008, step 0, loss = 2.00345396996, accuracy = 0.140000000596
Epoch 14, weight train batch 1009, step 1, loss = 1.830930233, accuracy = 0.180000007153
Epoch 14, weight train batch 1010, step 2, loss = 1.81476354599, accuracy = 0.360000014305
Epoch 14, weight train batch 1011, step 3, loss = 2.04306221008, accuracy = 0.159999996424
Epoch 14, struct train step 254, loss = 1.95434689522, accuracy = 0.241999998689
Epoch 14, weight train batch 1012, step 0, loss = 2.10470151901, accuracy = 0.219999998808
Epoch 14, weight train batch 1013, step 1, loss = 1.79848718643, accuracy = 0.439999997616
Epoch 14, weight train batch 1014, step 2, loss = 2.06086039543, accuracy = 0.239999994636
Epoch 14, weight train batch 1015, step 3, loss = 1.987377882, accuracy = 0.280000001192
Epoch 14, struct train step 255, loss = 1.96359539032, accuracy = 0.230000004172
Epoch 14, weight train batch 1016,

Epoch 14, weight train batch 1083, step 3, loss = 1.92037081718, accuracy = 0.280000001192
Epoch 14, struct train step 272, loss = 1.92865371704, accuracy = 0.247999995947
Epoch 14, weight train batch 1084, step 0, loss = 1.98366856575, accuracy = 0.159999996424
Epoch 14, weight train batch 1085, step 1, loss = 1.95134556293, accuracy = 0.280000001192
Epoch 14, weight train batch 1086, step 2, loss = 2.00046300888, accuracy = 0.159999996424
Epoch 14, weight train batch 1087, step 3, loss = 2.08786654472, accuracy = 0.20000000298
Epoch 14, struct train step 273, loss = 1.91389262676, accuracy = 0.25799998641
Epoch 14, weight train batch 1088, step 0, loss = 1.90080857277, accuracy = 0.300000011921
Epoch 14, weight train batch 1089, step 1, loss = 2.00008606911, accuracy = 0.219999998808
Epoch 14, weight train batch 1090, step 2, loss = 1.88304567337, accuracy = 0.300000011921
Epoch 14, weight train batch 1091, step 3, loss = 2.06271481514, accuracy = 0.259999990463
Epoch 14, struct trai

In [ ]:
inputs_test, targets_test = mnist.test.next_batch(10000)
inputs_test = inputs_test.reshape((-1, 28, 28, 1))
accs = []
for i in range(10):
    feed_dict = {model.inputs: inputs_test[i*1000:(i+1)*1000, ...], 
                 model.targets: targets_test[i*1000:(i+1)*1000, ...]}
    acc = model.sess.run(model.accuracy, feed_dict=feed_dict)
    accs.append(acc)
    
print(sum(accs)/10)

In [ ]:
import csv
with open('./log/results.csv', 'a+') as f:
    writer = csv.writer(f)
    writer.writerow(model.train_losses)
    writer.writerow(model.valid_losses)

In [ ]:
feed_dict = {model.inputs: inputs_train[0 : 32, ...],
             model.targets: targets_train[0 : 32, ...]}
print(model.pred)
print(model.sess.run(model.pred, feed_dict = feed_dict))
print(model.sess.run(model.targets, feed_dict = feed_dict))
print(model.struct_train_op)

In [ ]:
inputs_train, targets_train = mnist.train.next_batch(55000)
a = (targets_train.shape)
print(a)

In [6]:
mu = 4.3
sigma = 4

L = (np.ceil(mu-sigma)+np.floor(mu)-2*mu) / (2*sigma)
R = (2*mu-np.ceil(mu)-np.floor(mu+sigma)) / (2*sigma)

h_inv = (np.floor(mu)-np.floor(mu-sigma))*(L+1) + (np.floor(mu+sigma)-np.floor(mu))*(R+1)
  
h = 1 / h_inv

y = lambda x: -h/sigma * np.absolute(x-mu) + h

k = 0
for i in np.arange(np.ceil(mu-sigma), mu+sigma):
    k = k + y(i)
print k    
    

1.0000000000000002


In [67]:
rates = tf.cast(tf.range(tf.ceil(1.5), 4.1), tf.int32)
with tf.Session() as sess:
    print rates.eval()

[2 3 4]


In [68]:
[20] * 9

[20, 20, 20, 20, 20, 20, 20, 20, 20]